### **어텐션 가중치(attention weights)**
- 선형 결합을 통한, 전체 시퀀스의 가중 합 **weighted sum**
    $$ x'_{i} = \sum_{j=1}^{n} w_{ji}x_{j}$$
    - $ x'_{i} : \text{linear combination} $ (선형 결합)
    - $ w_{ji}$ : $ \text{attention weights} $ (계수(Coefficient))
    - **softmax 함수 이용** 하여 $ \text{attention weights} $ 총합이 1
    - **weighted sum** ($ \Sigma_{j=1}^{n} w_{ji}x_{j} $) 는 $w_{ji}$ 와 $x_{j}$ 의 **유사도(similarity)**
        - 즉 **가중치** = **유사도** 에 softmax(정규화)를 적용하여 얻은 값
    - 선형 결합으로 생성된 임베딩 $ x'_{i}$ : **문맥 고려 임베딩(contextualized embedding)**


### seq2seq 의 attention 매커니즘(인코더 디코더 어텐션)

![seq2seq with attention](https://github.com/tommyjin2894/KDT_project2/blob/main/0_2_3%20%EC%A1%B0%20%EB%AA%A8%EB%8D%B8%20%EA%B5%AC%EC%A1%B0%20%EC%84%A4%EB%AA%85%EB%8F%84_1.png?raw=true)

[사용 예시 프로젝트2 : 혐호 표현 분류 모델 (seq2seq with attention)](https://github.com/tommyjin2894/KDT_project2)

- 인코더
    ```py
    encoder_inputs = Input(shape=(max_text_len,))
    encoder_embedding = Embedding(corpus_size, embedding_size1, trainable=True, mask_zero=True)(encoder_inputs)
    encoder_dropout = Dropout(dropout_ratio)(encoder_embedding)
    encoder_lstm1 = Bidirectional(LSTM(lstm_size, return_state=True, return_sequences=True))
    encoder_outputs, forward_h, forward_c, backward_h, backward_c = encoder_lstm1(encoder_dropout)
    ```

- 디코더
    ```py
    decoder_inputs = Input(shape=(max_summary_len,))
    decoder_embedding_layer = Embedding(corpus_size_answer, embedding_size2, trainable=True, mask_zero=True)
    decoder_embedding = decoder_embedding_layer(decoder_inputs)
    decoder_dropout = Dropout(dropout_ratio)(decoder_embedding)
    decoder_lstm1 = LSTM(lstm_size*2, return_sequences=True, return_state=True)
    decoder_outputs, _, _ = decoder_lstm1(decoder_dropout, initial_state=encoder_states)
    decoder_outputs = Dropout(dropout_ratio)(decoder_outputs)
    ```

- 어텐션 레이어
    ```py
    attention_layer = Attention()
    attention_result = attention_layer([decoder_outputs, encoder_outputs])
    decoder_concat_input = Concatenate(axis=-1)([decoder_outputs, attention_result])
    ```

- 출력층
    ```py
    decoder_dense = Dense(corpus_size_answer, activation='softmax')
    decoder_outputs = decoder_dense(decoder_concat_input)
    ```
    
- 모델 정의
    ```py
    model = Model([encoder_inputs, decoder_inputs], decoder_outputs)
    model.compile(optimizer='adam', loss='sparse_categorical_crossentropy', metrics=['accuracy'])
    ```

- 어텐션 레이어의 계산

   0. **기존식 확인**
      $$ x'_{i} = \sum_{j=1}^{n} w_{ji}x_{j}$$
   1. **어텐션 스코어 계산**:
      - $ \text{Attention Score} = h_t \cdot h_s^T $

   2. **소프트맥스 적용**:
      - 어텐션 스코어에 소프트맥스를 적용하여 가중치 $ \alpha_s $로 변환.
      - $ \alpha_s \text{ as } w_{ji} = \text{softmax}\left(\frac{h_t \cdot h_s^T}{\sqrt{d_h}}\right)$
      - 여기서 $ d_h $는 hidden state의 차원.

   3. **출력 계산**:
      - 가중치 $ \alpha_s $를 인코더의 출력 $ h_s $에 곱하여 최종 출력을 계산.
      $$ \text{Output} = \sum_{s=1}^{S} \alpha_s \cdot h_s $$
   4. 여기에서 인코더의 $h_s$ 는 $K$(Key) 와 $V$(Value) 역할, 디코더의 $h_t$ 는 $Q$(Query)의 역할

### 기존 seq2seq 및 + attention 이용의 단점
- 순차적 특성으로 인하여 병렬 처리 불가(병렬에 유리한 gpu기능의 제약적 활용)
    - 순차적인 학습으로 인하여 경사 소실 문제가 발생 문제.
- bidirectional lstm을 이용함에도 한계점이 있다. 또한 여전히 순차적인 계산 이용한다.
- attention 층의 과부하
    - 모든 층의 hs cs를 concat 하여 계산하기 때문에 시퀀스가 길어짐에 따라 과부하가 걸린다.

### [트랜스 포머](https://arxiv.org/pdf/1706.03762)
![transformers](https://i.sstatic.net/BpxYv.png)

|순서|인코더 부분|디코더 부분|
|---|---|---|
|0|입력 임베딩 + 포지셔널 인코딩|입력 임베딩 + 포지셔널 인코딩|
|1|셀프 어텐션 (멀티 헤드 어텐션) |마스크드 셀프 어텐션 (멀티 헤드 어텐션)|
|2|잔차 연결|잔차 연결|
|3|레이어 정규화|레이어 정규화|
|4|피드 포워드 네트워크|디코더-인코더 어텐션 (멀티 헤드 어텐션)|
|5|잔차 연결|잔차 연결|
|6|레이어 정규화|레이어 정규화|
|7|인코더의 출력|피드 포워드 네트워크|
|8||잔차 연결|
|9||레이어 정규화|
|10||선형 층|
|11||소프트맥스 출력|

- 참고 : 논문에서의 멀티헤드 어텐션은 8개 


### 다양한 트랜스 포머 모델들
- **Encoder** + **Decoder** : t5
- **Encoder** 모델 : Bert 류 등
    * 양방향 어텐션(bidirectional attention)
- **Decoder** 모델 : gpt 류 등
    * 자기 회귀 어텐션(autoregressive attention)


### **셀프 어텐션**

![image.png](https://img.notionusercontent.com/s3/prod-files-secure%2F1f406a34-9833-41b3-af5a-06ebe0821494%2F21f6d610-d50d-4e43-b38d-27b010a1153a%2F1_self_attention.svg/size/?exp=1731833224&sig=-78EuHKYI03NfVZHf57uJkKR1m8ghm-5BOYRelCDV0U)

- **스케일드 닷 어텐션(점곱 어텐션)** 

    1. **Positional Embedding 생성 (위치정보)**

    2. **쿼리(Q), 키(K), 밸류(V)의 프로젝션**:
        - 입력 X와 가중치 행렬 $ W_Q, W_K, W_V $를 곱하여 프로젝션
        $$
        Q = XW_Q, \quad K = XW_K, \quad V = XW_V
        $$

    3. **어텐션 점수 계산**:
        - 쿼리(Q)와 키(K)의 내적(dot product)을 계산
        - 스케일 안정성을 위해 $\sqrt{d_k}$로 나눔
        $$
        \text{score}(i,j) = Q_i \cdot K_j^T
        $$
        $$
        \text{score\_scaled}(i, j) = \frac{Q_i \cdot K_j^T}{\sqrt{d_k}}
        $$
        - 여기서 $d_k$는 입력 벡터 차원수

    4. **어텐션 가중치(attention weights) 계산**:
        - 스케일된 점수를 소프트맥스 함수를 통해 변환하여 어텐션 가중치 계산:
        $$
        w_{ij} = \text{softmax}(\text{score\_scaled}(i, j))
        $$
        $$
        = \text{softmax}\left(\frac{Q_i \cdot K_j^T}{\sqrt{d_k}}\right)
        $$

    5. **토큰 임베딩 업데이트 (어텐션 출력)**:
        - 어텐션 가중치를 통해 밸류(V)의 가중 평균을 계산하여 새로운 출력 벡터를 생성:
            $$
            x'_{i} = \sum_{j=1}^{n} w_{ij} v_{j}
            $$

        - 행렬 표현:
            $$
            X' \text{(output vector)} = \text{softmax}\left(\frac{Q \cdot K^T}{\sqrt{d_k}}\right) \cdot V
            $$
        
        - 요소별 표현:
            $$
            x'_i \text{(output vector)} = \sum_{j=1}^{n} \text{softmax}\left(\frac{q_i \cdot k_j^T}{\sqrt{d_k}}\right) v_j
            $$

            - $i$는 쿼리 벡터의 인덱스
            - $j$는 키 벡터의 인덱스
            - $d_k$는 키 벡터의 차원

    6. 최종 결과를 **weighted sum** 이라고 한다.

### 어텐션 시각화

In [1]:
from transformers import AutoTokenizer
from bertviz.transformers_neuron_view import BertModel
from bertviz.neuron_view import show

model_ckpt = "bert-base-uncased"
tokenizer = AutoTokenizer.from_pretrained(model_ckpt)
model = BertModel.from_pretrained(model_ckpt)
text = "time flies like an arrow"
show(model, "bert", tokenizer, text, display_mode="light", layer=0, head=8)

/home/tommy/anaconda3/envs/transformer/lib/python3.11/site-packages/bertviz/transformers_neuron_view/modeling_utils.py:482: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  sta

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### 밀집 임베딩 만들기
- 밀집 :
    - one hot encoding 의 sparse 와 정 반대의 말
    - 즉 모든 행열 요소가 0이 아니다.

In [2]:
inputs = tokenizer(text, return_tensors="pt", add_special_tokens=False)
inputs

{'input_ids': tensor([[ 2051, 10029,  2066,  2019,  8612]]), 'token_type_ids': tensor([[0, 0, 0, 0, 0]]), 'attention_mask': tensor([[1, 1, 1, 1, 1]])}

In [3]:
from torch import nn
from transformers import AutoConfig

config = AutoConfig.from_pretrained(model_ckpt)
token_embedding = nn.Embedding(config.vocab_size, config.hidden_size)


In [4]:
input_imbeddings = token_embedding(inputs.input_ids) # 밀집 임베딩

### 셀프 어텐션 구하기(임베딩 된 벡터들을 이용하여 유사도 계산)
$$ \text{Attention score} = \frac{Q_i \cdot K_j^T}{\sqrt{d_k}} $$

In [5]:
import torch
from math import sqrt

q = k = v = input_imbeddings
d_k = k.size(-1) # k 의 차원
attention_score = torch.bmm(q, k.transpose(1,2))/sqrt(d_k) # 단순 행렬 곱

In [6]:
# 어텐션 점수 행렬 생성
attention_score.size()

torch.Size([1, 5, 5])

$$ \text{weight} = \text{softmax}(\text{Attention score}) $$

In [7]:
from torch.nn.functional import softmax

weight = softmax(attention_score, dim=-1)
weight

tensor([[[1.0000e+00, 7.9749e-14, 5.7128e-13, 4.2725e-12, 4.3887e-13],
         [1.7365e-13, 1.0000e+00, 5.3172e-13, 1.0742e-12, 2.5526e-13],
         [1.2077e-12, 5.1624e-13, 1.0000e+00, 6.1714e-13, 1.3360e-12],
         [8.7055e-12, 1.0052e-12, 5.9483e-13, 1.0000e+00, 1.4068e-12],
         [1.9679e-12, 5.2568e-13, 2.8339e-12, 3.0960e-12, 1.0000e+00]]],
       grad_fn=<SoftmaxBackward0>)

$$ \text{scaled dot producted} = \text{weight} \cdot V_j $$


In [8]:
output_vector = torch.bmm(weight,v)
output_vector

tensor([[[ 1.8739,  0.4459,  0.6107,  ..., -1.2471,  2.2166, -2.2507],
         [-0.0839,  0.2289, -1.1465,  ..., -0.7799, -0.2963,  0.8577],
         [ 0.1379, -0.0407, -0.0982,  ..., -1.3579, -1.2310,  0.3637],
         [-0.9403,  0.9920,  0.6579,  ...,  2.0550, -1.7559, -0.2119],
         [-0.4673,  0.5058,  0.4060,  ..., -0.3772,  0.4399, -0.4549]]],
       grad_fn=<BmmBackward0>)

$$ \therefore x'_i \text{(output vector)} = \sum_{j=1}^{n} \text{softmax}\left(\frac{Q_i \cdot K_j^T}{\sqrt{d_k}}\right) \cdot V_j $$

In [9]:
# 함수 정의로 나타낸다면
def scaled_dot_product_attention(q,k,v):
    d_k = k.size(-1)
    attention_score = torch.bmm(q, k.transpose(1,2)) / sqrt(d_k)
    weights= softmax(attention_score, dim=-1)
    return torch.bmm(weights, v) # 행렬 곱(내적) 자체에 sum 이 있기 때문에 이 자체로 weighted sum 이다

In [10]:
scaled_dot_product_attention(q,k,v)

tensor([[[ 1.8739,  0.4459,  0.6107,  ..., -1.2471,  2.2166, -2.2507],
         [-0.0839,  0.2289, -1.1465,  ..., -0.7799, -0.2963,  0.8577],
         [ 0.1379, -0.0407, -0.0982,  ..., -1.3579, -1.2310,  0.3637],
         [-0.9403,  0.9920,  0.6579,  ...,  2.0550, -1.7559, -0.2119],
         [-0.4673,  0.5058,  0.4060,  ..., -0.3772,  0.4399, -0.4549]]],
       grad_fn=<BmmBackward0>)

### bert-base-uncased의 어텐션 헤드 출력 확인
- 하나의 어텐션 헤드 : 특정 특징을 잡아내는 cnn 의 필터와 비슷한 역할을 한다.

In [11]:
from torch import nn
from transformers import AutoConfig

config = AutoConfig.from_pretrained(model_ckpt)
token_embedding = nn.Embedding(config.vocab_size, config.hidden_size)

In [12]:
config

BertConfig {
  "_name_or_path": "bert-base-uncased",
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "gradient_checkpointing": false,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "pad_token_id": 0,
  "position_embedding_type": "absolute",
  "transformers_version": "4.46.2",
  "type_vocab_size": 2,
  "use_cache": true,
  "vocab_size": 30522
}

In [13]:
# 단일 헤드 어텐션
class AttentionHead(nn.Module):
    def __init__(self, embed_dim, head_dim):
        super().__init__()
        self.q = nn.Linear(embed_dim, head_dim)
        self.k = nn.Linear(embed_dim, head_dim)
        self.v = nn.Linear(embed_dim, head_dim)

    def forward(self, hidden_state):
        atten_output = scaled_dot_product_attention(
            self.q(hidden_state), self.k(hidden_state), self.v(hidden_state))
        return atten_output
    
# 멀티 헤드 어텐션
class MultiHeadAttention(nn.Module):
    def __init__(self, config):
        super().__init__()
        embed_dim = config.hidden_size          # 768
        num_heads = config.num_attention_heads  # 12
        head_dim = embed_dim // num_heads       # 64
        self.heads = nn.ModuleList(
            [AttentionHead(embed_dim, head_dim) for _ in range(num_heads)]
        )
        self.output_linear = nn.Linear(embed_dim, embed_dim)

    def forward(self, hidden_state):
        x = torch.cat([h(hidden_state) for h in self.heads], dim=-1)
        x = self.output_linear(x)
        return x

In [14]:
miltihead_attn = MultiHeadAttention(config)
attn_output = miltihead_attn(input_imbeddings)
attn_output.size()

torch.Size([1, 5, 768])

In [15]:
from bertviz import head_view
from transformers import AutoModel

model = AutoModel.from_pretrained(model_ckpt, output_attentions = True)

text_1 = "im a good man."
text_2 = "im a friend of good man."

viz_input = tokenizer(text_1,text_2,return_tensors="pt")
atten =  model(**viz_input).attentions
text_2_start = (viz_input.token_type_ids == 0).sum(dim=1)
tokens = tokenizer.convert_ids_to_tokens(viz_input.input_ids[0])

head_view(atten, tokens, text_2_start, heads=[8])

2024-11-19 13:37:27.194445: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1731991047.219457   35842 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1731991047.225997   35842 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-11-19 13:37:27.247032: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
BertSdpaSelfAttention is used but `torch.nn.functional.scaled_dot_product_attention` does not support non-absolute `position_

<IPython.core.display.Javascript object>

### Position Wise Feed Forward Layer
- 각 위치별 완전 연결 층
    - 임베딩의 4배, GELU 이용

In [16]:
class FeedForward(nn.Module):
    def __init__(self, config):
        super().__init__()
        # hidden_size = 768, intermediate_size = 3072
        self.linear_1 = nn.Linear(config.hidden_size, config.intermediate_size)
        self.linear_2 = nn.Linear(config.intermediate_size, config.hidden_size)
        self.gelu = nn.GELU()

        # hidden_dropout_prob = 0.1
        self.dropout = nn.Dropout(config.hidden_dropout_prob) 

    def forward(self, x):
        x = self.linear_1(x)
        x = self.gelu(x)
        x = self.linear_2(x)
        x = self.dropout(x)
        return x

### 층 정규화 및 스킵 커넥션

- 사후 층 정규화

    ![after.png](images/03_01.png)
    - 상대적으로 불안정한 훈련
    - 학습률 웜-업 이 필요하다.
    - 그래디언트 발산의 위험이 있다.

- 사전 층 정규화

    ![before.png](images/03_02.png)
    - 안정적 훈련
    - 학습률 웜-업 이 필요없다.

### 인코더 구현

- 사전 층 정규화 이용

In [17]:
class TransformerEncoder(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.norm1= nn.LayerNorm(config.hidden_size)
        self.norm2= nn.LayerNorm(config.hidden_size)
        self.attention = MultiHeadAttention(config)
        self.feed_forward = FeedForward(config)
    
    def forward(self, x):
        hidden_state = self.norm1(x)
        x = x + self.attention(hidden_state) # skip connection
        x = x + self.feed_forward(self.norm2(x)) # skip connection
        return x


In [18]:
encoder_layer = TransformerEncoder(config)
encoder_layer

TransformerEncoder(
  (norm1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
  (norm2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
  (attention): MultiHeadAttention(
    (heads): ModuleList(
      (0-11): 12 x AttentionHead(
        (q): Linear(in_features=768, out_features=64, bias=True)
        (k): Linear(in_features=768, out_features=64, bias=True)
        (v): Linear(in_features=768, out_features=64, bias=True)
      )
    )
    (output_linear): Linear(in_features=768, out_features=768, bias=True)
  )
  (feed_forward): FeedForward(
    (linear_1): Linear(in_features=768, out_features=3072, bias=True)
    (linear_2): Linear(in_features=3072, out_features=768, bias=True)
    (gelu): GELU(approximate='none')
    (dropout): Dropout(p=0.1, inplace=False)
  )
)

### 위치 임베딩 추가하기

- 다양한 위치 임베딩 
    - **절대 위치 표현 (Absolute Positional Encoding)** : 각 토큰을 특정 위치에 고정
        - 이진법과 유사한 주기성을 가짐
        $$ PE(pos, 2i) = \sin\left(\frac{pos}{10000^{\frac{2i}{d_{model}}}}\right) $$
        $$ PE(pos, 2i+1) = \cos\left(\frac{pos}{10000^{\frac{2i}{d_{model}}}}\right) $$
        여기서 $ d_{model} $ 는 임베딩의 차원 수
        - 특징 :
            - Transformers 논문에 소개된 인코딩 방법
            - 고정된 위치에서의 정밀한 위치정보 제공
            - 이동 불변성 (Moving Invariance) : 시퀀스의 길이가 변하면 상대적인 위치정보가 반영되지 못함

    - **상대 위치 표현 (Relative Positional Encoding)** : 토큰 간의 거리 또는 관계 표현
        - 각 token 간의 상대적인 거리 또는 위치 정보를 인코딩하며, 주로 attention 메커니즘 통합(합산 : Summed).
            - token 간의 상대적 거리를 나타내는 추가적인 값을 통합(+)하여 attention score를 계산.
        - 특징 :
            - 시퀀스의 길이에 영향을 덜 받음, 문맥의 변동성이 큰 NLP 작업에서 보다 유연하고 일반화된 성능.
            - 더 복잡한 계산과 구현이 필요고, 상대 위치 정보가 명시적으로 수치화되지 않을 가능성이 있다.

- 비교 :
    - **절대 위치 표현**은 명시적인 위치 정보를 제공하며, **상대 위치 표현**은 다양한 문맥에서 더 유연하고 적응적인 관계를 나타냄.

In [85]:
class Embeddings(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.token_embeddings = nn.Embedding(config.vocab_size,
                                             config.hidden_size)
        self.pos_e = nn.Embedding(config.max_position_embeddings,
                                  config.hidden_size)
        self.layer_norm = nn.LayerNorm(config.hidden_size, eps=1e-12) # 수치적 안정성을 위해
        self.dropout = nn.Dropout()

    def forward(self, input_ids):
        seq_length = input_ids.size(1)
        posi_ids = torch.arange(seq_length, dtype=torch.long).unsqueeze(0) # unsqeeze 차원 추가
        token_embeddings = self.token_embeddings(input_ids)
        posit_embeddings = self.pos_e(posi_ids)
        # summed를 이용하여 합산
        embeddings = token_embeddings + posit_embeddings
        embeddings = self.layer_norm(embeddings)
        embeddings = self.dropout(embeddings)
        return embeddings

### 상대적 위치 표현을 포함한 트랜스 포머의 인코더

In [86]:
class TransformerEncoder_with_p(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.embeddings = Embeddings(config)
        self.layers = nn.ModuleList([TransformerEncoder(config)
                                     for _ in range(config.num_hidden_layers)])
    def forward(self, x):
        x = self.embeddings(x)
        for layer in self.layers:
            x = layer(x)
        return x

In [87]:
T_encoder_with_p = TransformerEncoder_with_p(config)
T_encoder_with_p # 바디 완성

TransformerEncoder_with_p(
  (embeddings): Embeddings(
    (token_embeddings): Embedding(30522, 768)
    (pos_e): Embedding(512, 768)
    (layer_norm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
    (dropout): Dropout(p=0.5, inplace=False)
  )
  (layers): ModuleList(
    (0-11): 12 x TransformerEncoder(
      (norm1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (norm2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (attention): MultiHeadAttention(
        (heads): ModuleList(
          (0-11): 12 x AttentionHead(
            (q): Linear(in_features=768, out_features=64, bias=True)
            (k): Linear(in_features=768, out_features=64, bias=True)
            (v): Linear(in_features=768, out_features=64, bias=True)
          )
        )
        (output_linear): Linear(in_features=768, out_features=768, bias=True)
      )
      (feed_forward): FeedForward(
        (linear_1): Linear(in_features=768, out_features=3072, bias=True)
        (linear_

### 분류 헤드 추가하기

In [94]:
inputs
tokenizer.convert_ids_to_tokens(inputs.input_ids[0])

['time', 'flies', 'like', 'an', 'arrow']

In [95]:
inputs.input_ids

tensor([[ 2051, 10029,  2066,  2019,  8612]])

In [ ]:
class Transformer_seq_classification(nn.Module):
    def __init__(self, config):
        super().__init__()
        self.encoder = TransformerEncoder_with_p(config)
        self.dropout = nn.Dropout(config.hidden_dropout_prob)
        self.classifier = nn.Linear(config.hidden_size, config.num_labels)
    
    def forward(self, x):
        x = self.encoder(x)[:,0,:]
        x = self.dropout(x)
        x = self.classifier(x)
        return x
    
config.num_labels = 3 # 분류 테스크 지정
encoder_classifier = Transformer_seq_classification(config)
encoder_classifier(inputs.input_ids)

tensor([[ 1.4293,  0.2945, -0.0952]], grad_fn=<AddmmBackward0>)

### 디코더 의 어텐션
- 인코더 디코더 어텐션

- 마스크드 멀티헤드 셀프 어텐션
    - 입력값의 mask 값을 -inf 로 하여 softmax 에서 0으로 수렴하게 된다.

In [114]:
seq_len = inputs.input_ids.size(-1)
seq_len

5

In [ ]:
mask = torch.tril(torch.ones(seq_len,seq_len)).unsqueeze(0)
mask

tensor([[[1., 0., 0., 0., 0.],
         [1., 1., 0., 0., 0.],
         [1., 1., 1., 0., 0.],
         [1., 1., 1., 1., 0.],
         [1., 1., 1., 1., 1.]]])

In [ ]:
attention_score.masked_fill(mask==0, -float("inf")) # 정의된 mask 기준 0을 마스킹


tensor([[[28.4854,    -inf,    -inf,    -inf,    -inf],
         [-1.6745, 27.7073,    -inf,    -inf,    -inf],
         [ 0.2945, -0.5554, 27.7368,    -inf,    -inf],
         [ 2.3066,  0.1478, -0.3768, 27.7737,    -inf],
         [ 0.0308, -1.2892,  0.3955,  0.4840, 26.9849]]],
       grad_fn=<MaskedFillBackward0>)

In [249]:
for i in range(seq_len):
    print(f"""\
        tokens :{tokenizer.convert_ids_to_tokens(inputs.input_ids[0])[:i+1]},
        attention_scores : {[[round(k, 2) for k in j]
          for j in attention_score.masked_fill(mask==0, -float("inf"))[:,i].tolist()]}
        """)

        tokens :['time'],
        attention_scores : [[28.49, -inf, -inf, -inf, -inf]]
        
        tokens :['time', 'flies'],
        attention_scores : [[-1.67, 27.71, -inf, -inf, -inf]]
        
        tokens :['time', 'flies', 'like'],
        attention_scores : [[0.29, -0.56, 27.74, -inf, -inf]]
        
        tokens :['time', 'flies', 'like', 'an'],
        attention_scores : [[2.31, 0.15, -0.38, 27.77, -inf]]
        
        tokens :['time', 'flies', 'like', 'an', 'arrow'],
        attention_scores : [[0.03, -1.29, 0.4, 0.48, 26.98]]
        


In [ ]:
def scaled_dot_product_attention_with_mask(q,k,v,mask=None):
    d_k = k.size(-1)
    attention_score = torch.bmm(q, k.transpose(1,2)) / sqrt(d_k)
    #--- 마스크층 추가
    if mask is not None:
        attention_score = attention_score.masked_fill(mask == 0, -float("inf"))
    #---
    weights= softmax(attention_score, dim=-1)
    return torch.bmm(weights, v)



In [307]:
q.size()

torch.Size([1, 5, 768])

In [305]:
mask = torch.tril(torch.ones(q.size()[1],q.size()[1])).unsqueeze(0)
mask.size()

torch.Size([1, 5, 5])

In [ ]:
scaled_dot_product_attention_with_mask(k,q,v, mask=mask) # weighted sum with mask

tensor([[[ 1.8739,  0.4459,  0.6107,  ..., -1.2471,  2.2166, -2.2507],
         [-0.0839,  0.2289, -1.1465,  ..., -0.7799, -0.2963,  0.8577],
         [ 0.1379, -0.0407, -0.0982,  ..., -1.3579, -1.2310,  0.3637],
         [-0.9403,  0.9920,  0.6579,  ...,  2.0550, -1.7559, -0.2119],
         [-0.4673,  0.5058,  0.4060,  ..., -0.3772,  0.4399, -0.4549]]],
       grad_fn=<BmmBackward0>)